### Older Dataset with IconClass Notation
These first blocks of code were written with the explorative intention of resolving and using as discrete qualitative data the natural language description of the iconclass notation, being this one chosen as a descriptive method to list all the iconographic elements of an artwork.

In [1]:
import pandas as pd

df = pd.read_csv('./dataset_wikidata_works.csv')
df.head()

movement movementLabel  \
0  http://www.wikidata.org/entity/Q4692   Renaissance   
1  http://www.wikidata.org/entity/Q4692   Renaissance   
2  http://www.wikidata.org/entity/Q4692   Renaissance   
3  http://www.wikidata.org/entity/Q4692   Renaissance   
4  http://www.wikidata.org/entity/Q4692   Renaissance   

                                artist        artistLabel  \
0  http://www.wikidata.org/entity/Q762  Leonardo da Vinci   
1  http://www.wikidata.org/entity/Q762  Leonardo da Vinci   
2  http://www.wikidata.org/entity/Q762  Leonardo da Vinci   
3  http://www.wikidata.org/entity/Q762  Leonardo da Vinci   
4  http://www.wikidata.org/entity/Q762  Leonardo da Vinci   

                                   works worksLabel  \
0  http://www.wikidata.org/entity/Q12418  Mona Lisa   
1  http://www.wikidata.org/entity/Q12418  Mona Lisa   
2  http://www.wikidata.org/entity/Q12418  Mona Lisa   
3  http://www.wikidata.org/entity/Q12418  Mona Lisa   
4  http://www.wikidata.org/entity/Q12418  Mona Lisa   

                                  symbols   symbolsLabel iconclass  \
0     http://www.wikidata.org/entity/Q527            sky       NaN   
1    http://www.wikidata.org/entity/Q8502       mountain       NaN   
2   http://www.wikidata.org/entity/Q12280         bridge       NaN   
3   http://www.wikidata.org/entity/Q15324  body of water       NaN   
4  http://www.wikidata.org/entity/Q107425      landscape       NaN   

                                    genre genreLabel  
0  http://www.wikidata.org/entity/Q134307   portrait  
1  http://www.wikidata.org/entity/Q134307   portrait  
2  http://www.wikidata.org/entity/Q134307   portrait  
3  http://www.wikidata.org/entity/Q134307   portrait  
4  http://www.wikidata.org/entity/Q134307   portrait

In [18]:
#api test
import requests as rq
import json

request = rq.get('https://iconclass.org/%s.json'%('95A(SISYPHUS)6'))
json = request.json()
json['txt']['en']

'suffering, misfortune of Sisyphus'

In [31]:
# to resolve the iconclass id to natural language

iconclass = df['iconclass'].fillna('')
print(iconclass)

def iconclass_resolution(iconclass_series):
    ids = dict()
    natural_series = list()
    for i in iconclass_series:
        if i == '':
            natural_series.append('empty')
        elif i in ids:
            natural_series.append(ids[i])
        else:
            try:
                request = rq.get('https://iconclass.org/%s.json'%(i))
                json_data = request.json()
                text = json_data['txt']['en']
                print(text)
                natural_series.append(text)
                ids[i] = text
            except:
                print(f'{i} this code is not working')
    return pd.Series(natural_series)

iconclass_resolution(iconclass_series=iconclass)

0         
1         
2         
3         
4         
        ..
33992     
33993     
33994     
33995     
33996     
Name: iconclass, Length: 33997, dtype: object
adoration of the Christ-child by Mary
horse
saints
the conversion of St. Eustace: while hunting (on horseback) he is confronted with a stag bearing a crucifix between its antlers; Eustace is shown kneeling before the stag (that appears on a rock)
hoofed animals: deer
rodents: hare
border, ribbon, braid
hunting dogs
spur
adult woman
St. George and the dragon: dressed in armour and mounted on a (white) horse he brandishes his sword (his lance lies already broken on the ground); the princess nearby may be shown praying or fleeing
Christ-child looking or turning to Mary ~ Madonna-representations
the Annunciation: Mary sitting
baptism of Christ in the river Jordan: John the Baptist pouring out water on Christ's head: the Holy Ghost descends
Tobias and the angel Raphael travelling, accompanied by Tobias' dog
forest, wood
a woma

0        empty
1        empty
2        empty
3        empty
4        empty
         ...  
33674    empty
33675    empty
33676    empty
33677    empty
33678    empty
Length: 33679, dtype: object

## Newer Dataset, guess what...without IconClass notation 
These blocks will perform some exploratory and manipulative operations on the renewed dataset, it is in fact necessary to have nice visualization and truly understand the quantitative nature of the dataset itself.

It is extracted from wikidata, we used mainly the wikidata query endpoint (https://query.wikidata.org), it has a built-in query system to rapidly browse properties and classes.

The dataset itself presents some limitations that will be further discussed.

```
select ?movement ?movementLabel ?movstart ?movend ?artist ?artistLabel (group_concat (?viafart) as ?viafartist)
?works ?worksLabel  (group_concat (?viafwork) as ?viafworks)
?symbols ?symbolsLabel ?genre ?genreLabel

where {

    {?artist wdt:P106 wd:Q1028181 .} UNION {?artist wdt:P106 wd:Q1925963 .}
    {?artist wdt:P135 ?movement .}
    optional {?movement wdt:P580 ?movstart .}
    optional {?movement wdt:P582 ?movend .}
    {?artist wdt:P800 ?works .}
    optional {?artist wdt:P214 ?viafart .}
    # only paintings, drawings, fresco paintings{?works wdt:P31 wd:Q3305213 .} UNION {?works wdt:P31 wd:Q134194 .} UNION {?works wdt:P31 wd:Q93184 .}
    {?2dart wdt:P279 wd:Q110304307 .}
    {?works wdt:P31 ?2dart .}
    optional {?works wdt:P136 ?genre .}
    optional {?works wdt:P214 ?viafwork .}
    {?works wdt:P180 ?symbols .} # union {?works wdt:P1257 ?iconclass .}
    SERVICE wikibase:label {bd:serviceParam wikibase:language "en".}

}
group by ?movement ?movementLabel ?movstart ?movend ?artist ?artistLabel ?works ?worksLabel ?symbols ?symbolsLabel ?iconclass ?genre ?genreLabel
```




In [1]:
#dataset import and description

import pandas as pd

df = pd.read_csv('./dataset_wikidata.csv')

print(df.info())
print(df.describe())

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 24336 entries, 0 to 24335
Data columns (total 17 columns):
 #   Column         Non-Null Count  Dtype 
---  ------         --------------  ----- 
 0   movement       24336 non-null  object
 1   movementLabel  24336 non-null  object
 2   movstart       11567 non-null  object
 3   movend         10635 non-null  object
 4   inception      7014 non-null   object
 5   artist         24336 non-null  object
 6   artistLabel    24336 non-null  object
 7   viafartist     24122 non-null  object
 8   works          24336 non-null  object
 9   worksLabel     24336 non-null  object
 10  viafworks      1748 non-null   object
 11  symbols        24336 non-null  object
 12  symbolsLabel   24336 non-null  object
 13  genre          22837 non-null  object
 14  genreLabel     22837 non-null  object
 15  mainsubj       8904 non-null   object
 16  mainsubjLabel  8904 non-null   object
dtypes: object(17)
memory usage: 3.2+ MB
None
                            

In [3]:
#grouping per movement and labels + counts

work_group = df.groupby('worksLabel')

symbols_group = df.groupby('symbolsLabel')
df_symbols_freq = symbols_group.count()
print(df_symbols_freq.to_string())

                                                                              movement  movementLabel  movstart  movend  inception  artist  artistLabel  viafartist  works  worksLabel  viafworks  symbols  genre  genreLabel  mainsubj  mainsubjLabel
symbolsLabel                                                                                                                                                                                                                                          
1750–75 clothing                                                                     2              2         2       2          0       2            2           2      2           2          0        2      2           2         0              0
1775–95 in Western fashion                                                           2              2         2       2          0       2            2           2      2           2          0        2      2           2         2              2
1793        

In [4]:
#10 movements with highest number of authors

movements_group = df.groupby(['symbolsLabel','movementLabel'])
print(movements_group.count().to_string())

                                                                                                                     movement  movstart  movend  inception  artist  artistLabel  viafartist  works  worksLabel  viafworks  symbols  genre  genreLabel  mainsubj  mainsubjLabel
symbolsLabel                                                                 movementLabel                                                                                                                                                                                    
1750–75 clothing                                                             Rococo                                         2         2       2          0       2            2           2      2           2          0        2      2           2         0              0
1775–95 in Western fashion                                                   Rococo                                         2         2       2          0       2            2           2

In [26]:
# correct and generate datasets with time series

time = list()
for row in df.iterrows():
    if row['movstart']:
        time.append(row['movstart'])
    elif row['inception']:
        time.append(row['inception'])
    else:
        time.append('empty')

print(pd.Series(time))

TypeError: tuple indices must be integers or slices, not str